In [8]:
import random
import re
from datasets import load_dataset

def split_into_sentences(text):
    sentences = re.split(r'(?<!\w\.\w.)(?<![A-Z][a-z]\.)(?<=\.|\?)\s', text)
    return sentences

# Example usage:
text = "This is a sentence. And this is another sentence? Finally, this is the last sentence."
sentences = split_into_sentences(text)
print(sentences)

# Load dataset
dataset = load_dataset("zhengyun21/PMC-Patients")

l = []
c = 0
t = []

pred_1 = []
pred_2 = []

# Filter the dataset based on conditions
for i in range(len(dataset['train'])):
    if ('brain' in dataset['train'][i]['patient'] and 'MRI' in dataset['train'][i]['patient']):
        l.append(i)
    else:
        if (c < 4000):
            t.append(i)
            c += 1

# TO EXTRACT HISTORY OF THE FIRST PATIENT IN THE LIST, USE:
# dataset['train'][11]

osl = []
for i in range(2000):
    osl.append(dataset['train'][l[i]]['patient'])
    pred_1.append(1)

for j in range(4000):
    osl.append(dataset['train'][t[j]]['patient'])
    pred_1.append(0)

# LET US OBTAIN DATA ONLY UPTO MRI
l = []
c = 0
for i in range(len(osl)):
    c += 1
    t = split_into_sentences(osl[i])
    s = ""
    for j in range(len(t)):
        s += t[j]
        if 'MRI' in t[j]:
            break

    l.append(s)
    osl[i] = s

lis = osl
print(len(lis))
# Combine and shuffle the lists
combined = list(zip(lis, pred_1))
random.shuffle(combined)

# Unzip the shuffled lists
lis_shuffled, pred_1_shuffled = zip(*combined)

# Convert back to lists if needed
lis_shuffled = list(lis_shuffled)
pred_1_shuffled = list(pred_1_shuffled)

print(len(lis_shuffled))
lis = lis_shuffled
pred_1 = pred_1_shuffled


['This is a sentence.', 'And this is another sentence?', 'Finally, this is the last sentence.']
6000
6000


In [9]:
print(osl)


IOPub data rate exceeded.
The Jupyter server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--ServerApp.iopub_data_rate_limit`.

Current values:
ServerApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
ServerApp.rate_limit_window=3.0 (secs)



In [10]:
import re

# Assuming lis contains the text data
dataset = lis
final_list_of_sentences = []

for text in dataset:
    sentences = re.split(r'\.\s*', text)
    # Ensure sentences are non-empty and add a full stop back
    sentences = [sentence + '.' for sentence in sentences if sentence]

    # Tokenize each sentence into words and join them back into a single string
    tokenized_sentences = []
    for sentence in sentences:
        # Use regex to find words and convert to lower case
        tokens = re.findall(r'\b[\w-]+\b', sentence.lower())
        # Join tokens to form a cleaned sentence
        tokenized_sentence = ' '.join(tokens)
        tokenized_sentences.append(tokenized_sentence)

    # Append the tokenized sentences to the final list
    final_list_of_sentences.append(tokenized_sentences)

print(len(final_list_of_sentences))


6000


In [11]:
for i in range(len(final_list_of_sentences)):
    if not final_list_of_sentences[i]:
        print('hi')
    for j in range(len(final_list_of_sentences[i])):
        if (j < len(final_list_of_sentences[i]) and not final_list_of_sentences[i][j]):
            final_list_of_sentences[i].remove(final_list_of_sentences[i][j])

        
            


In [12]:
!pip install pytorch-crf

In [13]:
import torch 
import torch.nn as nn
import re
from torchcrf import CRF
from transformers import AutoTokenizer, AutoModel

# Define BiLSTM and MOD classes
class BiLSTM(nn.Module):
    def __init__(self):
        super(BiLSTM, self).__init__()
        self.input_size = 768
        self.hidden_size = 256
        self.num_layers = 2
        self.dropout = 0.3
        self.bilstm = nn.LSTM(input_size=self.input_size, hidden_size=128, 
                             num_layers=self.num_layers, batch_first=True, 
                             dropout=self.dropout, bidirectional=True)

    def forward(self, embeddings):
        lstm_out, _ = self.bilstm(embeddings)
        return lstm_out

class MOD(nn.Module):
    def __init__(self, input_size, num_labels):
        super(MOD, self).__init__()
        self.bilstm = BiLSTM()
        self.linear = nn.Linear(256, num_labels)
        self.crf = CRF(num_labels)

    def forward(self, x):
        lstm_output = self.bilstm(x)
        embeddings = self.linear(lstm_output)
        return embeddings

# Load BioBERT tokenizer and model
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
tokenizer = AutoTokenizer.from_pretrained("dmis-lab/biobert-v1.1")
biobert_model = AutoModel.from_pretrained("dmis-lab/biobert-v1.1").to(device)

# Load the trained model
model = MOD(768, 6).to(device)  # Ensure model is on the same device
model.load_state_dict(torch.load(r"/home/rvce/Downloads/HPCC/best_model.pth", map_location=device))
model.eval()

# Initialize lists for storing results
all_symptoms_ALL = []
symptoms_wout_duration_ALL = []
symptom_with_organ_ALL = []
new_dict_ALL = []

# Assuming final_list_of_sentences is already defined
for i in range(len(final_list_of_sentences)):    
    sentences = final_list_of_sentences[i]
    tsl_tokenized = []
    
    for sentence in sentences:
        tokens = re.findall(r'\b[\w-]+\b', sentence.lower())
        tsl_tokenized.append(tokens)
    
    vocab_test = []
    for sentence in tsl_tokenized:
        for token in sentence:
            if token not in vocab_test:
                vocab_test.append(token)
    
    word_embeddings = []
    for word in vocab_test:
        tokens = tokenizer(word, return_tensors="pt").to(device)
        with torch.no_grad():
            outputs = biobert_model(**tokens)
        embedding = outputs.last_hidden_state[0][0]
        word_embeddings.append(embedding)

    word_embeddings_test = torch.stack(word_embeddings).to(device)
    sentence_embeddings_test = []
    each_sentence = []
    
    for k in range(len(tsl_tokenized)):
        each_word_embeddings_test = []
        for token in tsl_tokenized[k]:
            word_embedding_tensor_test = word_embeddings_test[vocab_test.index(token)]
            each_word_embeddings_test.append(word_embedding_tensor_test)
        sentence_embeddings_test.extend(each_word_embeddings_test)
        each_sentence.append(each_word_embeddings_test)

    pred = []
    for j, sentence in enumerate(each_sentence):
        with torch.no_grad():
            print(i, j)
            # Stack the sentence tensors and move them to the device
            sentence_tensor = torch.stack(sentence).to(device).view(1, -1, 768)
            output = model(sentence_tensor)
            prediction = model.crf.decode(output)
            pred.append(prediction)

    # Create lists for different labels
    lis_1 = []
    lis_3 = []
    lis_4 = []
    lis_5 = []

    for i in range(len(pred)):
        l1 = {}
        l3 = {}
        l4 = {}
        l5 = {}
        prediction = pred[i]
        s = ''
        for k in range(len(prediction)):
            if prediction[k][0] != 0:
                s += tsl_tokenized[i][k] + ' '
            elif k != 0 and prediction[k][0] == 0:
                t = prediction[k-1][0]
                if t != 0:
                    if t == 1:
                        l1[s.strip()] = k
                    elif t == 2:
                        l1[s.strip()] = k
                    elif t == 3:
                        l3[s.strip()] = k
                    elif t == 4:
                        l4[s.strip()] = k
                    elif t == 5:
                        l5[s.strip()] = k
                    s = ''
        if prediction[-1][0] != 0:
            t = prediction[-1][0]
            if t == 1:
                l1[s.strip()] = len(prediction)
            elif t == 2:
                l1[s.strip()] = len(prediction)
            elif t == 3:
                l3[s.strip()] = len(prediction)
            elif t == 4:
                l4[s.strip()] = len(prediction)
            elif t == 5:
                l5[s.strip()] = len(prediction)

        lis_1.append(l1)
        lis_3.append(l3)
        lis_4.append(l4)
        lis_5.append(l5)

    symptoms_wout_duration = []
    for l1 in lis_1:
        if l1:
            for key in l1.keys():
                symptoms_wout_duration.append(key)
    
    new_dict = {}
    for i in range(len(lis_3)):
        if not lis_3[i]:
            #new_dict_ALL.append(new_dict)
            continue
        for key_3, value_3 in lis_3[i].items():
            closest_key = None
            minimum_difference = float('inf')
            for key_1, value_1 in lis_1[i].items():
                difference = abs(value_3 - value_1)
                if difference < minimum_difference:
                    minimum_difference = difference
                    closest_key = key_1
            new_dict[key_3] = closest_key

    all_symptoms_ALL.append(symptoms_wout_duration)
    symptoms_wout_duration_ALL.append(symptoms_wout_duration)
    new_dict_ALL.append(new_dict)

print(all_symptoms_ALL)
print(symptoms_wout_duration_ALL)
print(symptom_with_organ_ALL)
print(new_dict_ALL)


/tmp/ipykernel_349438/1909730745.py:42: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.
  model.load_state_dict(torch.load(r"/home/rvce/Downloads/HPCC/best_model.pth", map_locat

0 0
0 1
0 2
0 3
0 4
0 5
0 6
0 7
0 8
0 9
0 10
0 11
0 12
0 13
0 14
0 15
0 16
0 17
1 0
1 1
1 2
2 0
2 1
2 2
2 3
2 4
2 5
2 6
2 7
2 8
2 9
2 10
2 11
2 12
2 13
2 14
2 15
2 16
2 17
2 18
2 19
2 20
2 21
2 22
2 23
2 24
2 25
2 26
3 0
3 1
3 2
3 3
3 4
3 5
3 6
3 7
3 8
3 9
3 10
3 11
3 12
3 13
3 14
3 15
3 16
3 17
3 18
3 19
3 20
3 21
3 22
3 23
3 24
3 25
3 26
3 27
3 28
3 29
3 30
3 31
3 32
3 33
3 34
3 35
3 36
3 37
3 38
3 39
3 40
3 41
3 42
3 43
3 44
3 45
3 46
3 47
3 48
3 49
3 50
3 51
3 52
3 53
3 54
3 55
3 56
3 57
3 58
3 59
3 60
3 61
3 62
3 63
3 64
3 65
3 66
3 67
3 68
3 69
3 70
3 71
3 72
3 73
3 74
3 75
3 76
3 77
3 78
3 79
3 80
3 81
3 82
3 83
3 84
3 85
3 86
3 87
3 88
3 89
3 90
3 91
3 92
3 93
3 94
3 95
3 96
3 97
3 98
3 99
3 100
3 101
3 102
3 103
4 0
4 1
4 2
4 3
4 4
4 5
4 6
4 7
4 8
4 9
4 10
4 11
4 12
4 13
4 14
4 15
4 16
4 17
4 18
4 19
4 20
4 21
4 22
4 23
5 0
5 1
5 2
5 3
6 0
6 1
6 2
6 3
6 4
6 5
6 6
6 7
6 8
6 9
6 10
6 11
6 12
6 13
6 14
6 15
6 16
6 17
6 18
6 19
6 20
6 21
6 22
6 23
6 24
6 25
7 0
7 1
7 2
7 3
7 4
7 5

IOPub data rate exceeded.
The Jupyter server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--ServerApp.iopub_data_rate_limit`.

Current values:
ServerApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
ServerApp.rate_limit_window=3.0 (secs)



In [14]:
all_symptoms_ALL = [list(set(lst)) for lst in all_symptoms_ALL]
print(all_symptoms_ALL)


[['masses', 'peripancreatic fat infiltration', 'proteinuria', 'mucin production', 'pain', 'mass', 'enlarged', 'fat', 'nucleoli', 'gland formation', 'areas', 'malignant cells', 'vascular involvement', 'hyperchromatic', 'infiltration', 'progression of', 'mass superior to the umbilicus', 'cytoplasm', 'nausea', 'decreased', 'lesions', 'malignancy'], ['intracerebral hemorrhagic metastases', 'numbness', 'left upper extremity weakness', 'neurological deficits'], ['asymptomatic', 'apical hypertrophy', 'left bundle branch block', 'st segment changes', 'left sternal chest pain', 'impaired relaxation pattern', 'pain', 'stenotic', 't wave inversions', 'dyspnea palpitations dizziness', 'chest pain', 'resting comfortably', 'hypertensive crisis', 'left ventricular cavity', 'sensation of', 'left ventricular hypertrophy', 'symptoms', 'high', 'occluding lesions', 'loss of consciousness', 'definity', 'lesions', 'changes', 'hypertension'], ['anuria', 'diastolic flow', 'asphyxia', 'to', 'bleeding', 'tachyp

In [15]:
l = []
for i in range(len(new_dict_ALL) - 1):
    if new_dict_ALL[i] != new_dict_ALL[i + 1]: 
        l.append(new_dict_ALL[i])
    
l.append(new_dict_ALL[len(new_dict_ALL) - 1])

symptom_with_duration_ALL = l


In [16]:
time_units = ['seconds', 'minutes', 'hours', 'days', 'months', 'years', 'decades']

def replace_keys(data, time_units):
    new_data = []
    for item in data:
        new_item = {}
        for key, value in item.items():
            matched_word = next((unit for unit in time_units if unit in key), None)
            if matched_word and value is not None:
                new_item[matched_word] = value
        new_data.append(new_item)
    return new_data

updated_data = replace_keys(symptom_with_duration_ALL, time_units)
print(updated_data)

symptom_with_duration_ALL = updated_data


[{'months': 'decreased'}, {}, {}, {'hours': 'collapsed'}, {}, {}, {}, {}, {'months': 'erectile dysfunction'}, {'months': 'sudden loss of consciousness'}, {}, {'days': 'diuresis'}, {}, {'days': 'swelling'}, {}, {'days': 'body aches'}, {}, {}, {}, {'months': 'fever pain'}, {}, {'years': 'weight gain'}, {}, {'months': 'seizure'}, {'days': 'hearing loss'}, {}, {}, {'decades': 'dependent traits'}, {}, {}, {}, {}, {}, {}, {'months': 'wound closure'}, {}, {}, {}, {'days': 'liver mass'}, {'months': 'behavior changes'}, {}, {}, {}, {}, {'years': 'lesions', 'months': 'lesions'}, {}, {}, {}, {}, {'years': 'hypertension', 'days': 'discomforts'}, {}, {}, {'days': 'anorexia'}, {}, {'months': 'buttock pain'}, {}, {}, {}, {'years': 'right corneal ulcer'}, {}, {}, {}, {}, {}, {}, {}, {'days': 'drainage', 'hours': 'chyle leak'}, {}, {'days': 'edema', 'months': 'adverse event'}, {}, {}, {}, {}, {}, {}, {}, {}, {}, {}, {}, {}, {}, {'days': 'crispa'}, {}, {'years': 'nodules papules', 'months': 'tired'}, {}

In [17]:
print(symptom_with_duration_ALL)

[{'months': 'decreased'}, {}, {}, {'hours': 'collapsed'}, {}, {}, {}, {}, {'months': 'erectile dysfunction'}, {'months': 'sudden loss of consciousness'}, {}, {'days': 'diuresis'}, {}, {'days': 'swelling'}, {}, {'days': 'body aches'}, {}, {}, {}, {'months': 'fever pain'}, {}, {'years': 'weight gain'}, {}, {'months': 'seizure'}, {'days': 'hearing loss'}, {}, {}, {'decades': 'dependent traits'}, {}, {}, {}, {}, {}, {}, {'months': 'wound closure'}, {}, {}, {}, {'days': 'liver mass'}, {'months': 'behavior changes'}, {}, {}, {}, {}, {'years': 'lesions', 'months': 'lesions'}, {}, {}, {}, {}, {'years': 'hypertension', 'days': 'discomforts'}, {}, {}, {'days': 'anorexia'}, {}, {'months': 'buttock pain'}, {}, {}, {}, {'years': 'right corneal ulcer'}, {}, {}, {}, {}, {}, {}, {}, {'days': 'drainage', 'hours': 'chyle leak'}, {}, {'days': 'edema', 'months': 'adverse event'}, {}, {}, {}, {}, {}, {}, {}, {}, {}, {}, {}, {}, {}, {'days': 'crispa'}, {}, {'years': 'nodules papules', 'months': 'tired'}, {}

In [18]:
!pip install groq

huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)


In [20]:
from groq import Groq
import ast
import time
import re
import httpx  # Ensure you have httpx installed

# Initialize the Groq client
client = Groq(api_key="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")

# Constants
REQUESTS_PER_MINUTE = 30
REQUESTS_PER_SECOND = REQUESTS_PER_MINUTE / 60
TOKENS_PER_MINUTE = 30000
TOKENS_PER_SECOND = TOKENS_PER_MINUTE / 60
EXPECTED_TOKENS_PER_REQUEST = 200  # Estimate based on average usage

def organ(medical_text, symptoms):
    prompt = (
        f"Use the following medical text: {medical_text} "
        f"Now make a list of dictionaries with key as symptom and value as organ (the given text should mention a specific organ, if the medical text doesn't have an organ for that symptom make the value 'unspecified'). "
        f"Answer should be ['symptom1':'organ1','symptom2':'organ2',...and so on]. "
        f"Remember to use the symptoms in the list only: {symptoms}. "
        f"The key and value should be strictly present in the above text. No generation of generic organs. "
        f"Give me the final list of dictionaries. I mean a Python list of dictionaries only, not a string. "
        f"Strictly, each value should be in the medical text given or else make it 'unspecified' and the organ should be in one word. "
        f"Respond with only the list of dictionaries. Do not include any other text in your response."
    )
    response = client.chat.completions.create(
        messages=[
            {
                "role": "user",
                "content": prompt,
            }
        ],
        model="llama3-8b-8192",  # Changed to the correct model
    )
    final_summary = response.choices[0].message.content
    return final_summary

def parse_response(response):
    # Clean the response string
    response = response.strip()
    
    # Remove the leading and trailing brackets if any
    if response.startswith('['):
        response = response[1:]
    if response.endswith(']'):
        response = response[:-1]
    
    # Replace single quotes with double quotes
    response = response.replace("'", '"')
    
    # Regex pattern to match key-value pairs
    pattern = re.compile(r'"([^"]+)":\s*"([^"]+)"')

    # Find all matches
    matches = pattern.findall(response)

    # Build dictionaries from the extracted key-value pairs
    parsed_data = [{key.strip(): value.strip()} for key, value in matches]

    return parsed_data

def write_list_to_file(data_list, file_path):
    """Writes a list to a file in append mode, with each item on a new line."""
    with open(file_path, 'a') as file:  # Open file in append mode
        for item in data_list:
            file.write(f"{item}\n")

def organ_with_retry(medical_text, symptoms, retries=3):
    """Attempts to call the organ function with retry logic."""
    for attempt in range(retries):
        try:
            return organ(medical_text, symptoms)
        except (httpx.ReadTimeout, httpx.ConnectError) as e:
            print(f"Attempt {attempt + 1} failed: {e}")
            time.sleep(2 ** attempt)  # Exponential backoff
    print("Request failed after multiple attempts.")
    return []  # Return an empty list or handle as needed

# Define the file path
file_path = r"/home/rvce/Downloads/HPCC/output2.txt"

# Assuming all_symptoms_ALL and dataset are defined
symptom_with_organ_ALL = []
c = 0
for i in range(len(all_symptoms_ALL)):
    # Generate response for each dataset entry
    funResponse = organ_with_retry(dataset[i], all_symptoms_ALL[i])
    
    # Convert the response string to a Python list of dictionaries ':'
    try:
        symptom_with_organ = parse_response(funResponse)
        print(symptom_with_organ)
        print(c)
        write_list_to_file(symptom_with_organ, file_path)
        c += 1
        
        # Rate limiting: Delay to maintain requests per minute limit
        time.sleep(1 / REQUESTS_PER_SECOND)  # Delay to respect requests per second
        time.sleep(EXPECTED_TOKENS_PER_REQUEST / TOKENS_PER_SECOND)  # Delay to respect token limits
        
    except (SyntaxError, ValueError) as e:
        print(f"Error parsing response: {e}")
        break
        symptom_with_organ = []

    # Append the parsed data to the result list
    symptom_with_organ_ALL.append(symptom_with_organ)

# Initialize an empty list to store the key-value pairs
key_value_pairs = []

# Iterate through the list of dictionaries
for graph in symptom_with_organ_ALL:
    for item in graph:
        if isinstance(item, dict):  # Ensure the item is a dictionary
            for k, v in item.items():
                if v != 'unspecified':
                    key_value_pairs.append(f"{k}: {v}")                 

# Append the key-value pairs to the file
with open(file_path, 'a') as file:  # Use 'a' mode to append
    for pair in key_value_pairs:
        file.write(pair + '\n')


[{'masses': 'pancreas'}, {'pain': 'lower back'}, {'periumbilical region': 'unspecified'}, {'mucin production': 'pancreas'}, {'mass': 'pancreas'}, {'superior to the umbilicus': 'unspecified'}, {'vascular involvement': 'splenic artery and vein'}, {'proteinuria': 'kidneys'}, {'nucleoli': 'unspecified'}, {'progression of': 'disease'}, {'hyperchromatic': 'unspecified'}, {'infiltration': 'connective tissue'}, {'peritoneal cancer': 'peritoneum'}, {'peripancreatic fat': 'pancreas'}, {'liver': 'liver'}, {'ilac lymph nodes': 'unspecified'}, {'gland formation': 'pancreas'}, {'cytoplasm': 'unspecified'}, {'nausea': 'unspecified'}, {'decreased': 'food intake'}, {'lesions': 'liver'}, {'malignancy': 'unspecified'}]
0
[{'symptom': 'left upper extremity weakness'}, {'organ': 'unspecified'}, {'symptom': 'numbness'}, {'organ': 'unspecified'}, {'symptom': 'intracerebral hemorrhagic metastases'}, {'organ': 'brain'}, {'symptom': 'neurological deficits'}, {'organ': 'brain'}]
1
[{'pain': 'chest'}, {'chest pai

BadRequestError: Error code: 400 - {'error': {'message': 'Please reduce the length of the messages or completion.', 'type': 'invalid_request_error', 'param': 'messages', 'code': 'context_length_exceeded'}}

In [ ]:
print(all_symptoms_ALL)
print(symptom_with_organ_ALL)
print(symptom_with_duration_ALL)

In [ ]:
#skip index 1030 during trainin g


for i in range(1031, len(all_symptoms_ALL)):
    # Generate response for each dataset entry
    funResponse = organ_with_retry(dataset[i], all_symptoms_ALL[i])
    
    # Convert the response string to a Python list of dictionaries ':'
    try:
        symptom_with_organ = parse_response(funResponse)
        print(symptom_with_organ)
        print(c)
        write_list_to_file(symptom_with_organ, file_path)
        c += 1
        
        # Rate limiting: Delay to maintain requests per minute limit
        time.sleep(1 / REQUESTS_PER_SECOND)  # Delay to respect requests per second
        time.sleep(EXPECTED_TOKENS_PER_REQUEST / TOKENS_PER_SECOND)  # Delay to respect token limits
        
    except (SyntaxError, ValueError) as e:
        print(f"Error parsing response: {e}")
        break
        symptom_with_organ = []

    # Append the parsed data to the result list
    symptom_with_organ_ALL.append(symptom_with_organ)

# Initialize an empty list to store the key-value pairs
key_value_pairs = []

# Iterate through the list of dictionaries
for graph in symptom_with_organ_ALL:
    for item in graph:
        if isinstance(item, dict):  # Ensure the item is a dictionary
            for k, v in item.items():
                if v != 'unspecified':
                    key_value_pairs.append(f"{k}: {v}")                 

# Append the key-value pairs to the file
with open(file_path, 'a') as file:  # Use 'a' mode to append
    for pair in key_value_pairs:
        file.write(pair + '\n')

[{'stenosis': 'sinus'}, {'massage': 'unspecified'}, {'headache': 'unspecified'}, {'papilledema': 'optic nerve'}, {'blurry vision nausea': 'unspecified'}, {'flattening': 'sclera'}, {'prelaminar optic nerve distension': 'optic nerve'}, {'posterior sclera enhancement': 'sclera'}, {'vertical tortuosity': 'orbital optic nerve'}, {'intact': 'unspecified'}, {'vomiting': 'unspecified'}]
1030
[{'painful': 'face'}, {'fever': 'unspecified'}, {'peritoneal effusion': 'unspecified'}, {'ventricular enlargement': 'brain'}, {'abnormality': 'coagulation'}, {'flowery': 'skin'}, {'left intracerebral hemorrhage': 'brain'}, {'swollen': 'abdomen'}]
1031
[{'symptom': 'sudden weakness'}, {'organ': 'right hand'}, {'symptom': 'hypoesthesia'}, {'organ': 'right hand'}, {'symptom': 'hypoesthesia'}, {'organ': 'right lower limb'}, {'symptom': 'weakness'}, {'organ': 'right lower limb'}, {'symptom': 'gait ataxia'}, {'organ': 'unspecified'}, {'symptom': 'neurological deficits'}, {'organ': 'unspecified'}]
1032
[{'air': '

In [23]:
all_symptoms_ALL

['enhancement',
 'allergic',
 'headache',
 'alert',
 'pinprick',
 'to',
 'cranial nerves deficits',
 'lesions',
 'nasal vision',
 'diplopia',
 'papilledema',
 'ptosis']

In [ ]:
import networkx as nx
import matplotlib.pyplot as plt

# Initialize a list to store graphs
graphs = []

# Process each patient's symptom data to create a graph
for i, patient_data in enumerate(symptom_with_organ_ALL):
    # Create a new graph
    G = nx.Graph()
    
    # Add a central node for the patient
    patient_node = f'Patient {i+1}'
    G.add_node(patient_node, label='Patient')
    
    # Add nodes for symptoms and connect them to the patient node
    for item in patient_data:
        for symptom, organ in item.items():
            if organ != 'unspecified':
                G.add_node(symptom, label='Symptom')
                G.add_edge(patient_node, symptom)
                # Add nodes for organs and connect them to the symptoms
                if organ != 'unspecified':
                    G.add_node(organ, label='Organ')
                    G.add_edge(symptom, organ)
            else:
                G.add_node(symptom, label='Symptom')
                G.add_edge(patient_node, symptom)

    # Optional: Set edge weights based on symptom durations
    if i < len(symptom_with_duration_ALL):
        for symptom, duration in symptom_with_duration_ALL[i].items():
            if G.has_edge(patient_node, symptom):
                G[patient_node][symptom]['weight'] = time_units.index(duration)

    # Append the graph for the patient to the list
    graphs.append(G)
# Plot each graph in the list
# for G in graphs:
#     plot_graph(G)


In [ ]:
print(graphs[0])

In [ ]:
from transformers import BertTokenizer, BertModel, BertConfig
import torch

# Load the tokenizer and model
config_path = r"/home/rvce/Downloads/HPCC/config.json"
vocab_path = r"/home/rvce/Downloads/HPCC/vocab.txt"
model_path = r"/home/rvce/Downloads/HPCC/pytorch_model.bin"


# Load configuration, tokenizer, and model
config = BertConfig.from_pretrained(config_path)
tokenizer = BertTokenizer.from_pretrained(vocab_path)
model = BertModel.from_pretrained(model_path, config=config, local_files_only=True)

# Move model to device
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
model.to(device)

# Define your text
text = "Patient 1"

# Tokenize the input text and move tensors to device
inputs = tokenizer(text, return_tensors='pt').to(device)

# Get the embeddings
with torch.no_grad():
    outputs = model(**inputs)
    embeddings = outputs.last_hidden_state

# Find the index of the 'patient' token
token_index = (inputs['input_ids'] == tokenizer.convert_tokens_to_ids('patient')).nonzero(as_tuple=True)[1].item()

# Extract the embedding for the 'patient' token
patient_embedding = embeddings[0, token_index]

# Print the shape and the embedding
print(patient_embedding.shape)
print(patient_embedding)


In [ ]:
from transformers import BertTokenizer, BertModel, BertConfig
import torch
import numpy as np

# Load the tokenizer and model
config_path = r"/home/rvce/Downloads/HPCC/config.json"
vocab_path = r"/home/rvce/Downloads/HPCC/vocab.txt"
model_path = r"/home/rvce/Downloads/HPCC/pytorch_model.bin"


config = BertConfig.from_pretrained(config_path)
tokenizer = BertTokenizer.from_pretrained(vocab_path)
model = BertModel.from_pretrained(model_path, config=config, local_files_only=True)

# Move model to device
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
model.to(device)

feature_matrices = []

for graph in graphs:
    matrix = []
    for node in graph.nodes():
        print(node)
        text = node  # Text to be tokenized
        inputs = tokenizer(text, return_tensors='pt').to(device)
        # print(inputs)

        with torch.no_grad():
            outputs = model(**inputs)
            embeddings = outputs.last_hidden_state

        print(embeddings.shape)
        # print(embeddings[0])

        # Averaging the embeddings
        averaged_matrix = embeddings[0].mean(dim=0).view(1, -1)
        print(averaged_matrix.shape)
        # print(averaged_matrix)

        matrix.append(averaged_matrix)

    matrix = torch.cat(matrix, dim=0)  # (num_nodes, hidden_size)
    feature_matrices.append(matrix)

# Convert feature_matrices to numpy array if needed
feature_matrices_np = [matrix.cpu().numpy() for matrix in feature_matrices]

# Print the numpy arrays
# print((feature_matrices_np))


In [ ]:
print(feature_matrices[0].shape)

In [ ]:
import torch

# Assuming `device` has been defined as before (CUDA or CPU)
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")

main_edge_list = []
lis = []

for G in graphs:
    matrix = []
    print(G.nodes)

    edge_list = list(G.edges())
    unique_nodes = set(node for edge in edge_list for node in edge)

    # Step 2: Create a mapping from node labels to integers
    node_mapping = {node: i for i, node in enumerate(unique_nodes)}

    # Convert edge list to numeric representation
    numeric_edge_list = [[node_mapping[u], node_mapping[v]] for u, v in edge_list]

    # Create tensor and move to the appropriate device
    edge_tensor = torch.tensor(numeric_edge_list, dtype=torch.long).to(device)
    lis.append(edge_tensor)

    # Store the edge list in main_edge_list
    main_edge_list.append(edge_list)

# Print the tensors
for edge_tensor in lis:
    print(edge_tensor)


In [ ]:
print(main_edge_list[0])
print(feature_matrices[0])
print(lis)

In [ ]:
print(lis[0].shape)
print(feature_matrices[0].shape)

In [ ]:
!pip install torch-geometric


In [ ]:
import torch
import torch.nn as nn
import torch.nn.functional as F
from torch_geometric.nn import GCNConv, SortAggregation
from torch_geometric.data import Data
import torch.optim as optim

# Define the device
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")

class GCN_SortPool_CNN(nn.Module):
    def __init__(self, in_channels, hidden_channels, out_channels, k):
        super(GCN_SortPool_CNN, self).__init__()
        self.conv1 = GCNConv(in_channels, hidden_channels)
        self.conv2 = GCNConv(hidden_channels, hidden_channels)
        self.sort_pool = SortAggregation(k=k)
        self.cnn1d = nn.Conv1d(in_channels=hidden_channels, out_channels=32, kernel_size=2)
        
        # Calculate the correct input size for the fully connected layer
        cnn_output_size = 32 * (k - 1)  # Because kernel_size=2 reduces length by 1
        self.fc = nn.Linear(cnn_output_size, out_channels)
        
    def forward(self, x, edge_index):
        # GCN Layers
        x = F.relu(self.conv1(x, edge_index))
        x = F.relu(self.conv2(x, edge_index))
        
        # SortPooling
        x = self.sort_pool(x, torch.zeros(x.size(0), dtype=torch.long, device=x.device))  # Create a dummy batch tensor
        
        # Reshape for 1D CNN
        x = x.view(x.size(0), -1, self.sort_pool.k)  # Reshape to (batch_size, hidden_channels, k)
        
        # 1D CNN
        x = F.relu(self.cnn1d(x))
        x = x.view(x.size(0), -1)  # Flatten
        
        # Fully Connected + Sigmoid
        x = self.fc(x)
        x = torch.sigmoid(x)  # Apply sigmoid activation
        return x

# Define your model
model = GCN_SortPool_CNN(in_channels=768, hidden_channels=32, out_channels=1, k=5).to(device)  # Move model to device

# Initialize optimizer and criterion
optimizer = optim.Adam(model.parameters(), lr=0.001)
criterion = nn.BCELoss()  # Binary Cross Entropy Loss for binary classification

# Assuming you have lists of feature matrices and edge lists with varying node counts
n = 4  # Example number of graphs

# Create a list of Data objects
graphs = [Data(x=feature_matrices[i].to(device), edge_index=lis[i].to(device)) for i in range(n)]  # Move data to device

# Training loop
pred_1 += pred_2
num_epochs = 1000
for epoch in range(num_epochs):
    model.train()
    total_loss = 0
    for i, graph in enumerate(graphs):
        optimizer.zero_grad()
        output = model(graph.x, graph.edge_index.view(2, -1))
        target = torch.tensor(pred_1[i], dtype=torch.float32, device=device).view(1, 1)  # Move target to device
        loss = criterion(output, target)
        loss.backward()
        optimizer.step()
        total_loss += loss.item()
    
    print(f"Epoch {epoch+1}, Average Loss: {total_loss / len(graphs)}")


In [ ]:
# After training loop (for example, after epoch 1000)
torch.save(model.state_dict(), 'gcn_sortpool_cnn.pth')


In [ ]:
print(device)